<div class="alert alert-block alert-info">
This notebook would not have been possible without the help and commitment of the open-source software community involved in Pangeo, Xarray, Dask, Numpy, OpenEO, Pandas, GeoPandas. Communities who act in the silence of the universe and make people marvel as they look at the opensource sky.
</div>

# Purpose

This notebook demonstrates how `Pangeo` and `Holoviz` open-source software stack facilitates computing and visualizing the Vegetation Condition Index (VCI) ([1] Kogan, 1995), a well-established indicator to estimate droughts from remote sensing data.

VCI compares the current normalized difference vegetation index (NDVI) \[2] to the range of values observed in previous years.

We will use Sentinel-3 NDVI Analisis Ready Data (ARD) and Long Term Statistics (1999-2019) product provided by the Copernicus Global Land Service \[3].

Both datasets are discovered through the OpenEO API\[5] from the CGLS distributor VITO \[4] and an [EGI registration](https://aai.egi.eu/) is needed.

Further info about drought indexes can be found in the Integrated Drought Management Programme \[5]

\[1] [Application of vegetation index and brightness temperature for drought detection](https://www.sciencedirect.com/science/article/abs/pii/027311779500079T)
\[2] [NDVI](https://en.wikipedia.org/wiki/Normalized_difference_vegetation_index)
\[3] [Copernicus Global Land Service](https://land.copernicus.eu/global/index.html)
\[4] [Vito](https://vito.be/en)
\[5] [OpenEO](https://openeo.org/)
\[5] [Integrated Drought Management](https://www.droughtmanagement.info/indices)

# Setup

Let's install `openeo`, an open source interface that facilitates standardized interchange between users and applications of Copernicus and other EO data as hosted by an increasing number of cloud providers.

In [1]:
import pkg_resources
if not any(list(map(lambda i: i.key == 'openeo', pkg_resources.working_set))):
    !pip install openeo

The libraries are grouped by their function with a short comment describing their main purpose. 

In [2]:
# data
import numpy as np #arrays
import pandas as pd #dataframes
import xarray as xr #multidimensional arrays
import geopandas as gpd #geospatial vector data
import openeo
import zarr

# visualization
import matplotlib.pyplot as plt
import holoviews as hv
import hvplot.xarray
import hvplot.pandas

# Data import

## Selection of Area of interest (AOI)

We define the area of interest using the Global Administrative Unit Layers [GAUL G2015_2014](https://data.apps.fao.org/map/catalog/srv/eng/catalog.search#/metadata/9c35ba10-5649-41c8-bdfc-eb78e9e65654) provided by FAO-UN (see [Documentation](https://data.apps.fao.org/map/catalog/srv/api/records/9c35ba10-5649-41c8-bdfc-eb78e9e65654/attachments/GAUL2015_Documentation.zip)).
[`GeoPandas`](https://geopandas.org/en/stable/), a python-based library extending the capabilities of [`Pandas`](https://pandas.pydata.org/) to deal with geometry and spatial operations, will help to manage geodata.

The official data distribution from FAO is through the WFS service (below how to retrieve data):

GAUL = gpd.read_file('https://data.apps.fao.org/map/gsrv/gsrv1/gaul/wfs?'
                     'service=WFS&version=2.0.0&'
                     'Request=GetFeature&'
                     'TypeNames=gaul:g2015_2014_2&'
                     'srsName=EPSG%3A4326&'
                     'maxFeatures=2500&'
                     'outputFormat=json')

Unfortunately seems that the service is pretty slow. As alternative to this approach the JRC MARS unit is distributing the original dataset that was in shapefile format. To faster the fetch Is strongly advise to use this approach.

In [3]:
GAUL = gpd.read_file('zip+https://mars.jrc.ec.europa.eu/asap/files/gaul1_asap.zip')

Data are organized in a tabular structure. For each element an index a data (made of columns) and a geometry is defined.

![](./images/dataframe.svg "table")

Geometry are defined through [shapely](https://shapely.readthedocs.io/en/stable/) geometry objects with three different basic classes:

Points | Multi-Points
Lines | Multi-Lines
Polygons | Multi-Polygons

In [ ]:
GAUL.head(5)

Slicing and sub-setting can be achieved through the same semantic as in `Pandas`. In the cell below, we subset the polygon geometry in which `name1` field equals to `Lombardia`.

In [ ]:
AOI_name = 'Lombardia'
AOI = GAUL[GAUL.name1 == AOI_name]
AOI_poly = AOI.geometry

`Geopandas` brings the possibility to interrogate vector-related attributes such as area, bounds, total_bounds, among others.

For a single object, like our AOI, the bounds can inform `max` and `min` coordinates on each axis. If multiple AOIs had been selected then total_bounds returns coordinates, but for the entire `GeoSeries`.

In [ ]:
AOI_min_lon, AOI_min_lat, AOI_max_lon, AOI_max_lat = AOI_poly.bounds.values.tolist()[0]

## Data fetch

Datasets can be downloaded directly through the [official portal](https://land.copernicus.eu/global/index.html) but, if not ordered through the legacy portal, files are in the order of 2GB each.

\# There are two main technologies to explore and retread datasets. STAC and openEO. More or less they are similar but here, the VITO's openEO service, at the time of writing, isn't fully compatible with STAC we will
\# rely on openEO.
\# This will make possible to retreat just a portion of data and keep the process affordable even with low connections.

Note: OpenEO is an open application programming interface (API) that connects clients like R, Python and JavaScript to big Earth observation cloud back-ends. More infos [here](https://openeo.org/)
Authentication can be acheived through the [OIDC](https://openid.net/connect/) using the EGI credentials.

The ***BIGGEST*** difference between Xarray (and consequentially Pangeo) and openEO is that Xarray is ***domain-agnostic*** instead openEO, as the name suggest, is dedicated to the analysis of Earth Observation data.

In [ ]:
session = openeo.connect("https://openeo.vito.be").authenticate_oidc(provider_id="egi")

As all the libraries there is a catalog of the products that here are named as Collections.

In [ ]:
session.list_collections()

Metadata can be easily explored through a double click on the collection, or it can retract using the function .describe_collection()
'CGLS_NDVI300_V2_GLOBAL' stands for Copernicus Globa Land Service, NDVI index, 300m of nominal resolution, Version 2 of the algorithm and Global means Global coverage.

In [ ]:
session.describe_collection('CGLS_NDVI300_V2_GLOBAL')

Instead of request the entire dataset, to avoid useless transfer, a subset in time, space and band is requested.
In reality this is not going to download anything but is just a pointer to the data on the server.

In [ ]:
datacube = session.load_collection(
    'CGLS_NDVI300_V2_GLOBAL',
    spatial_extent={"west": AOI_min_lon, "south":AOI_min_lat , "east": AOI_max_lon, "north":AOI_max_lat },
    temporal_extent = ["2022-01-01", "2022-08-01"],
    bands=['NDVI']
)

To complete the request and trigger the download a specific function has to be called. As output GeoTiff format can be an alternative.
Once loaded with xarray there no evident difference between formats. COG, Geotiff, NetCDF, NetCDF Zarr can be easily read.

In [ ]:
datacube.download(f"./data/C_GLS_NDVI_20220101_20220701_{AOI_name}_S3_2.nc", format="NetCDF")

## Basic Concepts

- Dataset and DataArray
- open a NedCDF through Xarray
- understanding the difference between coordinates and dimensions
- Get access to a Variable in a Dataset
- Get access to the attributes
- Selection method
- Plotting

In [ ]:
cgls_ds= xr.open_dataset(f'./data/C_GLS_NDVI_20220101_20220701_{AOI_name}_S3_2.nc')

As the dataset is in NetCDF format the system automatically select the correct engine (this underneath has been
conducted through the automatic specification of engine='netcdf'). If the dataset could be in geoTiff format the engine would have been 'rasterio'.
Supposing that you have a dataset in an unrecognised format you can always create your own engine and pass it through the engine parameter.

Having a look to the content can reveal how data are structured

In [ ]:
cgls_ds

How Xarray is structured.

Data array
   - Dimension
   - Coordinates
   - Variables
   - Values
   - Attributes

Data set
    - Attributes


As later on other datasets has dimension named according to the more common triad lat,lon,time a renomination is needed.

In [ ]:
cgls_ds = cgls_ds.rename(x='lon', y='lat', t='time')

observe how the nomenclature has changed

In [ ]:
cgls_ds

DataArray, within Datasets, can be access through the dot notation like  Dataset.NameofVariable

In [ ]:
cgls_ds.NDVI

Same can be achieved for attributes but instead of a DataArray .attrs will return a dictionary.

In [ ]:
cgls_ds.NDVI.attrs

Memory must be always taken into account. Each DataArray has an impact on it and to avoid issues like kill the kernel users must avoid to open data bigger than memory.
If the dataset isn't fitting the available memory then the best option would be to load it through the help of Dask in a lazy approach. Later on we will introduce the concept
As the size of the data isn't too big we can continue without any problem.

In [ ]:
print(f'{np.round(cgls_ds.NDVI.nbytes / 1024**2, 2)} MB') # all the data are automatically loaded into memory

#### Selection methods

As underneath DataArrays are Numpy Array (that implements the standard Python x[obj] (x: array, obj: int,slice ) syntax) data can be retreated through the same approach of numpy indexing.

In [ ]:
cgls_ds.NDVI[0,100,100]

or slicing

In [ ]:
cgls_ds.NDVI[0:5,100:110,100:110]

As isn't really easy to remember the order of dimensions Xarray can really help making possible to select the position using names

.isel -> selection based on positional index
.sel  -> selection based on coordinates

A single point can be selected through the positional index and the dimension names

In [ ]:
cgls_ds.NDVI.isel(time=0, lat=100, lon=100) # same as cgls_ds.NDVI[:,-1,0]

The more common way to select a point is through the labeled coordinate using the .sel method.
Coordinates are always affected by precision issue so the best option would be to use the sampling method that will search for the closest point according to the method requested.

Option for the method are:
pad / ffill: propagate last valid index value forward
backfill / bfill: propagate next valid index value backward
nearest: use nearest valid index value

Another important parameter that can be set is the tolerance that specify the distance between original and the target. (abs(index\[indexer] - target) <= tolerance) from [documentation](https://xarray.pydata.org/en/v0.17.0/generated/xarray.DataArray.sel.html#:~:text=xarray.DataArray.sel%20%C2%B6%20DataArray.sel%28indexers%3DNone%2C%20method%3DNone%2C%20tolerance%3DNone%2C%20drop%3DFalse%2C%20%2A%2Aindexers_kwargs%29%20%C2%B6,this%20method%20should%20use%20labels%20instead%20of%20integers.)

In [ ]:
cgls_ds.NDVI.sel(time='2022-01-01')

time dimension is easy to be used as there is a 1 to 1 correspondence with value in the indexed, float values are not that easy to be use and a small difference makes a big difference in results.

In [ ]:
cgls_ds.NDVI.sel(lat=8.79935614, lon=46.33611286)

Original values are much longer to the one represented

In [ ]:
cgls_ds.NDVI[0,100,100].lon.values.item()

In [ ]:
cgls_ds.NDVI[0,100,100].lat.values.item()

In [ ]:
cgls_ds.NDVI.sel(lat='46.336112857142965', lon='8.799356142858498')

To make life easier a method can be selected to deal with inexact matches

In [ ]:
POI_lat = 45.88 ; POI_lon = 8.63

In [ ]:
cgls_ds.NDVI.sel(lat=POI_lat, lon=POI_lon, method='nearest')

As the exercise is more focus to an Area Of Interest this can be obtained through a bounding box defined with slices.

In [ ]:
NDVI_AOI = cgls_ds.NDVI.sel(lat=slice(AOI_max_lat,AOI_min_lat), lon=slice(AOI_min_lon,AOI_max_lon))

#### Plotting
Plotting data can be easily obtained through matplotlib.pyplot back-end [matplotlib documentation](https://matplotlib.org/stable/index.html)

In [ ]:
NDVI_AOI.isel(time=0).plot(cmap="RdYlGn")

Or through the HoloViews back-end thanks to the hvplot that acts as high-level plotting API

In [ ]:
NDVI_AOI[0].hvplot(cmap="RdYlGn", width=1000, height=1000)

Having a look to data distribution can reveal a lot about data

In [ ]:
NDVI_AOI[0].hvplot.hist(cmap="RdYlGn",bins=25, width=800, height=700)

Values are a little odd in comparison with standard NDVI range values \[-1, +1]. This finds confirmation on the max values reported in the [Product User Manual](https://land.copernicus.eu/global/sites/cgls.vito.be/files/products/CGLOPS1_PUM_NDVI300m-V2_I1.20.pdf) (PUM)

## NDVI characteristics from the Product User Manual (PUM)

| layer name  | description                             | physical min | physical max | digital max | scaling | offset | No Data  |
|-------------|-----------------------------------------|--------------|--------------|-------------|---------|--------|----------|
| ndvi        | normalized difference vegetation index  | -0.08        | 0.92         | 250         | 1/250   | -0.08  | 254, 255 |
| ndvi_unc    | uncertainty on ndvi                     | 0            | 1            | 1000        | 1/1000  | 0      | 65535    |
| nobs        | number of observations                  | 0	           | 32           | 32          | 1       | 0      | 255      |
| qflag       | bitwise quality flag                    | -            | -            | 254         | 1       | 0      | 255      |


from : [Copernicus Global Land Service NDVI 300 V2.0.1](https://land.copernicus.eu/global/sites/cgls.vito.be/files/products/CGLOPS1_PUM_NDVI300m-V2_I1.20.pdf)

## Basic Computations

- Arithmetics
- Reductions

Simple arithmetic can be obtained without worry about dimensions and coordinates. Automatically the numpy component will take to vectorize over all array values

In [ ]:
NDVI = cgls_ds.NDVI * (1/250) - 0.08

In [ ]:
NDVI

Same result can be achieved using the usual numpy functions.

In [ ]:
NDVI_ = np.subtract(np.multiply(cgls_ds.NDVI, (1/250)), 0.08)

In [ ]:
NDVI_

## Statistics

In [ ]:
NDVI.min()

In [ ]:
NDVI.max(dim='time')

## Aggregation

In [ ]:
NDVI_monthly = NDVI.groupby(NDVI.time.dt.month).mean()

In [ ]:
NDVI_monthly.month

## Mask

Not all values are valid and masking all the once not in the valid range \[-0.08, 0.92] is mandatory. Masking can be achieved through the method DataSet|Array.where(cond, other) or xr.where(cond, x, y)
The difference consist in the possibility to specify the value in case the condition is positive or not; .where doesn't give this possibility.

In [ ]:
NDVI_msked = NDVI.where((NDVI >= -0.08) & (NDVI <= 0.92)) # by default where condition is false values are set to NA

To better visualize the mask with the help of xr.where a specific variable can be constructed.

In [ ]:
NDVI_msk = xr.where((NDVI <= -0.08) | (NDVI >= 0.92), 1, 0)

In [ ]:
NDVI_msked.hvplot(groupby ='time', cmap="RdYlGn", width=800, height=700)

In [ ]:
NDVI_msk.hvplot(groupby = 'time', cmap="RdYlGn", width=800, height=700)

Plot a single point over the time dimension

In [ ]:
NDVI_msked.sel(lat=POI_lat, lon=POI_lon, method='nearest')\
    .hvplot(ylim=(-0.08, 0.92))

### Interpolation of nans
As the selection has reviled that there are some non-valid values Nans can be directly interpolated through the help of [scipy interpolation](https://docs.scipy.org/doc/scipy/tutorial/interpolate.html)

In [ ]:
NDVI_msked.sel(lat=POI_lat, lon=POI_lon, method='nearest')\
    .interpolate_na('time', method='linear')\
    .hvplot(ylim=(-0.08, 0.92))

Same can be applied as well over the time dimension

In [ ]:
NDVI_interp = NDVI_msked.interpolate_na('time', method='linear', max_gap=pd.to_timedelta(31, 'd'))

## Clipping data according to a polygon

one of the basic concept in GIS is to clip data using a vector geometry. Xarray isn't directly capable of dealing with vectors but thanks to rioxarray can be easily achieved
Rioxarray extends Xarray with all most of the plus that Rasterio (GDAL) brings.

First step that has to be defined is the reference system

In [ ]:
NDVI_msked = NDVI_interp.rio.write_crs(4326)

Once this has been done we can clip data with the polygon that has been read through geopandas at the beginning of the notebook.

In [ ]:
NDVI_AOI = NDVI_msked.rio.clip(AOI_poly, crs=4326)

Once data is limited to the AOI a histogram can be added to the visualization.

In [ ]:
NDVI_AOI.hvplot(groupby='time', cmap='RdYlGn', width=800, height=700 ).hist()

In [ ]:
NDVI_AOI

In [ ]:
#Proposal : start region '02_Introduction_to_Dask'

### Introduction to the Long Term statistics

CGLS LTS are computed over a time span of 20 years aggregated over each 10 days period (month/01,month/11, month/21). For each date the long term minimum, maximum, mean, median and standard deviation are computed.

In [ ]:
NDVI_LTS = xr.open_dataset(rf'.\data\CopernicusGlobalLand\LTS\c_gls_NDVI-LTS_1999-2019-0101_GLOBE_VGT-PROBAV_V3.0.1.nc')

In [ ]:
NDVI_LTS.sel(lat=POI_lat, lon=POI_lon, method='nearest')['min'].values

In [ ]:
LTS = xr.open_mfdataset(rf'.\data\CopernicusGlobalLand\LTS\*.nc', combine='nested', concat_dim=['time'], decode_coords="all")

In [ ]:
LTS

Note! If you use one of xarray’s open methods such as xarray.open_dataset to load netCDF files with the default engine, it is recommended to use decode_coords=”all”. This will load the grid mapping variable into coordinates for compatibility with rioxarray. From [rioxarray documentation](https://corteva.github.io/rioxarray/stable/getting_started/getting_started.html#xarray)


In [ ]:
LTS = LTS.rio.write_crs(4326)

In [ ]:
LTS = LTS.sel(lat=slice(AOI_max_lat,AOI_min_lat) ,lon=slice(AOI_min_lon,AOI_max_lon))

In [ ]:
LTS = LTS.rio.clip(AOI_poly, crs=4326)

In [ ]:
LTS

In [ ]:
LTS = LTS.chunk({'time':-1, 'lat':'5MB', 'lon':'5MB'})

As the time dimension is defined as 'year less' (don't forget that are aggregated values spanning between 1999 and 2019) to let Xarray align values, the index needs to be reformed to the current year.

In [ ]:
dates_2022 = pd.date_range('20220101', '20221231')
decadie = dates_2022[np.isin(dates_2022.day, [1,11,21])]
decadie

In [ ]:
LTS = LTS.assign_coords(time=decadie)

In [ ]:
LTS['min'][5].hvplot(geo=True)

In [ ]:
LTS['min'].sel(lat=POI_lat, lon=POI_lon, method='nearest').values

In [ ]:
LTS.to_zarr(rf'.\data\CopernicusGlobalLand\LTS\c_gls_NDVI-LTS_1999-2019-{AOI_name}_VGT-PROBAV_V3.zarr', mode='w', )

In [ ]:
LTS = xr.open_zarr(rf'.\data\CopernicusGlobalLand\LTS\c_gls_NDVI-LTS_1999-2019-{AOI_name}_VGT-PROBAV_V3.zarr')

In [ ]:
LTS_NDVI_POI = LTS.sel(lat=POI_lat, lon=POI_lon, method='nearest')

In [ ]:
POI_min = LTS_NDVI_POI['min']
POI_max = LTS_NDVI_POI['max']
POI_std = LTS_NDVI_POI['stdev']
POI_mean = LTS_NDVI_POI['mean']
POI = NDVI_AOI.sel(lat=POI_lat, lon=POI_lon, method='nearest')

+ merges graphs by putting them next to each other
* overlays graphs on one another to create one single graph combining all individual

In [ ]:
LTS_NDVI_POI['mean'].values

In [ ]:
POI_min = LTS_NDVI_POI['min']
POI_max = LTS_NDVI_POI['max']
POI_std = LTS_NDVI_POI['stdev']
POI_mean = LTS_NDVI_POI['mean']
POI = NDVI_AOI.sel(lat=POI_lat, lon=POI_lon, method='nearest')

+ merges graphs by putting them next to each other
* overlays graphs on one another to create one single graph combining all individual

In [ ]:
(POI.hvplot(width=1000, height=700, label='NDVI') *
 POI_mean.hvplot(c='grey', label='mean LTS 1999-2019', alpha=0.2, line_dash='dashed') *
 POI_min.hvplot(c='b',label='min LTS 1999-2019', alpha=0.2, line_dash='dashed') *
 POI_max.hvplot(c='r', label='Max LTS 1999-2019', alpha=0.2, line_dash='dashed') *
 hv.Area((POI_mean.time, POI_mean - 2 * POI_std, POI_mean + 2 * POI_std ), vdims=['- Std', '+ Std'], label='Standard deviation LTS 1999-2019',).opts( color='blue', alpha=0.2))\
    .opts(title=f"CGLS S3 300m NDVI fluctuation over the year 2022 in comparison with CGLS Long Term Statistics\nPoint of interest Lat {np.round(POI.lat.data,2)} Lon {np.round(POI.lon.data,2)}",
          legend_position='bottom_right')

Clip the dataset over the AOI

In [ ]:
LTS = LTS.rio.write_crs(4326)

In [ ]:
LTS = LTS.rio.clip(AOI_poly, crs=4326)

The nominal spatial resolution of the Long term statistics is 1km. As the current NDVI product has a nominal spatial resolution of 300m a re projection is needed.
RioXarray through RasterIO that wraps the GDAL method can take care of this.
More info about all the options can be found [here](https://rasterio.readthedocs.io/en/stable/api/rasterio.warp.html#rasterio.warp.reproject)

In [ ]:
NDVI_1k = NDVI_AOI.rio.reproject_match(LTS)

In [ ]:
NDVI_1k.coords

RioXarray does a great job, but it looses the coordinates names. To be able to combine different dataset coords needs to be renamed.

In [ ]:
NDVI_1k = NDVI_1k.rename({'x': 'lon', 'y':'lat'})

In [ ]:
NDVI_1k.coords

In [ ]:
# NDVI_1k = NDVI_1k.where((NDVI_1k >= -0.08) & (NDVI_1k <= 0.92))

In [ ]:
NDVI_1k.hvplot(groupby='time', cmap='RdYlGn', width=800, height=700)

The Vegetation Condition Index (VCI) compares the current NDVI to the range of values observed in the same period in previous years. The VCI is expressed in % and gives an idea where the observed value is situated between the extreme values (minimum and maximum) in the previous years.

In [ ]:
VCI = ((NDVI_1k - LTS['min']) / (LTS['max'] - LTS['min'])) * 100

In [ ]:
VCI.name = 'VCI'

In [ ]:
VCI_c = VCI.compute()

In [ ]:
VCI.isel(time=-1).plot()

In [ ]:
VCI.sel(lat=POI_lat, lon=POI_lon, method='nearest').hvplot.hist()

In [ ]:
VCI_c..isel(time=-1)(groupby='time', cmap='RdYlGn', alpha=0.7,
                         width=800, height=700)

In [ ]:
VCI_c.hvplot.contourf(cmap='RdYlGn', alpha=0.7,
                                    levels=[-200,-100,-50, 0,50,100,200],
                                    geo=True, tiles= 'CartoLight',
                                    width=800, height=700,
                                    title=f'CGLS VCI {AOI_name} {VCI.isel(time=-1).time.dt.date.data}')

In [99]:
VCI_c.hvplot.contourf(cmap='RdYlGn', alpha=0.7,
                                    levels=[-200,-100,-50, 0,50,100,200],
                                    geo=True, tiles= 'CartoLight',
                                    width=800, height=700,
                                    title=f'CGLS VCI {AOI_name} {VCI.isel(time=-1).time.dt.date.data}')

C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\geoviews\operation\projection.py:79: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  polys = [g for g in geom if g.area > 1e-15]


Traceback (most recent call last): 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\plotting\util.py", line 279, in get_plot_frame 
 return map_obj[key] 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\spaces.py", line 1217, in __getitem__ 
 val = self._execute_callback(*tuple_key) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\spaces.py", line 984, in _execute_callback 
 retval = self.callback(*args, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\spaces.py", line 582, in __call__ 
 ret = self.callable(*args, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\overlay.py", line 34, in dynamic_mul 
 element = other[args] 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\spaces.py", line 1217, in __getitem__ 
 val = self._execute_callback(*tuple_key) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\spaces.py", line 984, in _execute_callback 
 retval = self.callback(*args, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\spaces.py", line 582, in __call__ 
 ret = self.callable(*args, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\util\__init__.py", line 997, in dynamic_operation 
 return apply(obj, *key, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\util\__init__.py", line 989, in apply 
 processed = self._process(element, key, kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\util\__init__.py", line 973, in _process 
 return self.p.operation(element, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\hvplot\converter.py", line 1167, in method_wrapper 
 el = method(x, y, data=ds.data) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\hvplot\converter.py", line 2155, in contourf 
 contourf = self.contour(x, y, z, data, filled=True) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\hvplot\converter.py", line 2150, in contour 
 return (contours(qmesh, filled=filled, levels=levels) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\param\parameterized.py", line 3654, in __new__ 
 return inst.__call__(*args,**params) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\operation.py", line 220, in __call__ 
 return element.apply(self, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\accessors.py", line 45, in pipelined_call 
 result = __call__(*args, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\accessors.py", line 202, in __call__ 
 new_obj = apply_function(self._obj, **inner_kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\operation.py", line 214, in __call__ 
 return self._apply(element) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\operation.py", line 141, in _apply 
 ret = self._process(element, key) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\operation\element.py", line 590, in _process 
 zmin, zmax = element.range(2) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\data\__init__.py", line 204, in pipelined_fn 
 result = method_fn(*args, **kwargs) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\data\__init__.py", line 515, in range 
 lower, upper = self.interface.range(self, dim) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\data\xarray.py", line 311, in range 
 return finite_range(data, dmin, dmax) 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\holoviews\core\data\util.py", line 16, in finite_range 
 column = column[np.isfinite(column)] 
 File "C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\xarray\core\d

C:\Users\Pier\miniconda3\envs\foss4g\lib\site-packages\geoviews\operation\projection.py:79: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  polys = [g for g in geom if g.area > 1e-15]


:DynamicMap   [time]
   :Overlay
      .Tiles.I    :Tiles   [x,y]
      .Polygons.I :Polygons   [lon,lat]   (VCI)

In [ ]:
# Proposal : Start region 03_Exercise

### Execise: Using the Global Land Cover mask all the urban areas

In [ ]:
session.describe_collection('GLOBAL_LAND_COVER')

In [ ]:
datacube_LC = session.load_collection(
    'GLOBAL_LAND_COVER',
    spatial_extent={"west": AOI_min_lon, "south":AOI_min_lat , "east": AOI_max_lon, "north":AOI_max_lat },
    bands=['Discrete_Classification_map']
)

In [ ]:
datacube_LC.download(f"C_GLS_LC_20220101_20220701_{AOI_name}_PROBA_3.nc", format="NetCDF")

In [ ]:
cgls_LC= xr.open_dataset('C_GLS_LC_20220101_20220701_CENTRALITALY_3.nc')

In [ ]:
LC_2019 = cgls_LC.Discrete_Classification_map.sel(t='2019-01-01')

In [ ]:
LC_2019 = LC_2019.rio.write_crs(4326)

In [ ]:
LC_2019 = LC_2019.rio.reproject_match(LTS)

In [ ]:
LC_2019

In [ ]:
urban_mask = xr.where(LC_2019 == 50, False, True).rename({'x': 'lon', 'y':'lat'})

In [ ]:
urban_mask.hvplot(width=800, height=700)

In [ ]:
VCI_masked = VCI.where(urban_mask) 

In [ ]:
VCI_masked.name = 'VCI masked'

In [ ]:
VCI_masked.isel(time=0).hvplot(cmap='RdYlGn', alpha=0.7,
                                  geo=True, tiles= 'CartoLight',
                                  width=800, height=700,)